In [2]:
import pickle
import os
from perses.annihilation.rest import RESTTopologyFactory
from perses.annihilation.lambda_protocol import RESTState
from openmmtools.states import SamplerState, ThermodynamicState, CompoundThermodynamicState
from openmmtools import cache, utils
from perses.dispersed.utils import configure_platform
cache.global_context_cache.platform = configure_platform(utils.get_fastest_platform().getName())
from simtk import openmm, unit
import math
from openmmtools.constants import kB
from openmmtools import mcmc, multistate
import argparse
import copy
from perses.dispersed import feptasks
import mdtraj as md
import numpy as np
from perses.app.relative_point_mutation_setup import PointMutationExecutor

INFO:numexpr.utils:Note: NumExpr detected 48 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
INFO:numexpr.utils:NumExpr defaulting to 8 threads.


conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA


INFO:rdkit:Enabling RDKit 2021.03.4 jupyter extensions


In [3]:
outdir = "/data/chodera/zhangi/perses_benchmark/neq/14/130/"
phase = 'complex'
state = 1

In [4]:
length = 1
move_length = 1
timestep = 4
# radius = args.radius

# Load rhtf
i = os.path.basename(os.path.dirname(outdir))
path = os.path.join(outdir, f"{i}_{phase}_{state}.pickle")
htf = pickle.load(open(path, "rb" ))
positions = htf.hybrid_positions

In [32]:
traj = md.Trajectory(np.array(htf.hybrid_positions), htf.hybrid_topology)
RBD_chain = [atom.index for atom in htf.hybrid_topology.atoms if atom.residue.chain.index == 0] 
ACE2_chain = [atom.index for atom in htf.hybrid_topology.atoms if atom.residue.chain.index == 2] 
rbd_matches = md.compute_neighbors(traj, 0.5, ACE2_chain, haystack_indices=RBD_chain)
ace2_matches = md.compute_neighbors(traj, 0.5, RBD_chain, haystack_indices=ACE2_chain)
rest_atoms = list(rbd_matches[0]) + list(ace2_matches[0])

In [33]:
len(list(rbd_matches[0]) + list(ace2_matches[0]))

555

In [24]:
len(rbd_matches[0])

478

In [25]:
len(ace2_matches[0])

526

In [ ]:
distances, residue_pairs = md.compute_contacts(traj, contacts='all', scheme='closest-heavy')

In [ ]:
d = {residue.index: residue for residue in htf.hybrid_topology.residues}

In [10]:
len(residue_pairs)

266496

In [12]:
for chain in htf.hybrid_topology.chains:
    print(chain.index)
    for res in chain.residues:
        print(res)

0
ACE332
THR333
ASN334
LEU335
CYS336
PRO337
PHE338
GLY339
GLU340
VAL341
PHE342
NLN343
ALA344
THR345
ARG346
PHE347
ALA348
SER349
VAL350
TYR351
ALA352
TRP353
ASN354
ARG355
LYS356
ARG357
ILE358
SER359
ASN360
CYS361
VAL362
ALA363
ASP364
TYR365
SER366
VAL367
LEU368
TYR369
ASN370
SER371
ALA372
SER373
PHE374
SER375
THR376
PHE377
LYS378
CYS379
TYR380
GLY381
VAL382
SER383
PRO384
THR385
LYS386
LEU387
ASN388
ASP389
LEU390
CYS391
PHE392
THR393
ASN394
VAL395
TYR396
ALA397
ASP398
SER399
PHE400
VAL401
ILE402
ARG403
GLY404
ASP405
GLU406
VAL407
ARG408
GLN409
ILE410
ALA411
PRO412
GLY413
GLN414
THR415
GLY416
LYS417
ILE418
ALA419
ASP420
TYR421
ASN422
TYR423
LYS424
LEU425
PRO426
ASP427
ASP428
PHE429
THR430
GLY431
CYS432
VAL433
ILE434
ALA435
TRP436
ASN437
SER438
ASN439
ASN440
LEU441
ASP442
SER443
LYS444
VAL445
GLY446
GLY447
ASN448
TYR449
ASN450
TYR451
LEU452
TYR453
ARG454
LEU455
PHE456
ARG457
LYS458
SER459
ASN460
LEU461
LYS462
PRO463
PHE464
GLU465
ARG466
ASP467
ILE468
SER469
THR470
GLU471
ILE472
TYR473
GLN4

HOH2427
HOH2428
HOH2429
HOH2430
HOH2431
HOH2432
HOH2433
HOH2434
HOH2435
HOH2436
HOH2437
HOH2438
HOH2439
HOH2440
HOH2441
HOH2442
HOH2443
HOH2444
HOH2445
HOH2446
HOH2447
HOH2448
HOH2449
HOH2450
HOH2451
HOH2452
HOH2453
HOH2454
HOH2455
HOH2456
HOH2457
HOH2458
HOH2459
HOH2460
HOH2461
HOH2462
HOH2463
HOH2464
HOH2465
HOH2466
HOH2467
HOH2468
HOH2469
HOH2470
HOH2471
HOH2472
HOH2473
HOH2474
HOH2475
HOH2476
HOH2477
HOH2478
HOH2479
HOH2480
HOH2481
HOH2482
HOH2483
HOH2484
HOH2485
HOH2486
HOH2487
HOH2488
HOH2489
HOH2490
HOH2491
HOH2492
HOH2493
HOH2494
HOH2496
HOH2497
HOH2498
HOH2499
HOH2500
HOH2501
HOH2502
HOH2503
HOH2504
HOH2505
HOH2506
HOH2507
HOH2508
HOH2509
HOH2510
HOH2511
HOH2512
HOH2513
HOH2514
HOH2515
HOH2516
HOH2517
HOH2518
HOH2519
HOH2520
HOH2521
HOH2522
HOH2523
HOH2524
HOH2525
HOH2526
HOH2527
HOH2528
HOH2529
HOH2530
HOH2531
HOH2532
HOH2533
HOH2534
HOH2535
HOH2536
HOH2537
HOH2538
HOH2539
HOH2540
HOH2541
HOH2542
HOH2543
HOH2544
HOH2545
HOH2546
HOH2547
HOH2548
HOH2549
HOH2550
HOH2551
HOH2552


HOH4433
HOH4434
HOH4435
HOH4436
HOH4437
HOH4438
HOH4439
HOH4440
HOH4441
HOH4442
HOH4443
HOH4444
HOH4445
HOH4446
HOH4447
HOH4448
HOH4449
HOH4450
HOH4451
HOH4452
HOH4453
HOH4454
HOH4455
HOH4456
HOH4457
HOH4458
HOH4459
HOH4460
HOH4461
HOH4462
HOH4463
HOH4464
HOH4465
HOH4466
HOH4467
HOH4468
HOH4469
HOH4470
HOH4471
HOH4472
HOH4473
HOH4474
HOH4475
HOH4476
HOH4477
HOH4478
HOH4479
HOH4480
HOH4481
HOH4482
HOH4483
HOH4484
HOH4485
HOH4486
HOH4487
HOH4488
HOH4489
HOH4490
HOH4491
HOH4492
HOH4493
HOH4494
HOH4495
HOH4496
HOH4497
HOH4498
HOH4499
HOH4500
HOH4501
HOH4502
HOH4503
HOH4504
HOH4505
HOH4506
HOH4507
HOH4508
HOH4509
HOH4510
HOH4511
HOH4512
HOH4513
HOH4514
HOH4515
HOH4516
HOH4517
HOH4518
HOH4519
HOH4520
HOH4521
HOH4522
HOH4523
HOH4524
HOH4525
HOH4526
HOH4527
HOH4528
HOH4529
HOH4530
HOH4531
HOH4532
HOH4533
HOH4534
HOH4535
HOH4536
HOH4537
HOH4538
HOH4539
HOH4540
HOH4541
HOH4542
HOH4543
HOH4544
HOH4545
HOH4546
HOH4547
HOH4548
HOH4549
HOH4550
HOH4551
HOH4552
HOH4553
HOH4554
HOH4555
HOH4556
HOH4557


HOH6442
HOH6443
HOH6444
HOH6445
HOH6446
HOH6447
HOH6448
HOH6449
HOH6450
HOH6451
HOH6452
HOH6453
HOH6454
HOH6455
HOH6456
HOH6457
HOH6458
HOH6459
HOH6460
HOH6461
HOH6462
HOH6463
HOH6464
HOH6465
HOH6466
HOH6467
HOH6468
HOH6469
HOH6470
HOH6471
HOH6472
HOH6473
HOH6474
HOH6475
HOH6476
HOH6477
HOH6478
HOH6479
HOH6480
HOH6481
HOH6482
HOH6483
HOH6484
HOH6485
HOH6486
HOH6487
HOH6488
HOH6489
HOH6490
HOH6491
HOH6492
HOH6493
HOH6494
HOH6495
HOH6496
HOH6497
HOH6498
HOH6499
HOH6500
HOH6501
HOH6502
HOH6503
HOH6504
HOH6505
HOH6506
HOH6507
HOH6508
HOH6509
HOH6510
HOH6511
HOH6512
HOH6513
HOH6514
HOH6515
HOH6516
HOH6517
HOH6518
HOH6519
HOH6520
HOH6521
HOH6522
HOH6523
HOH6524
HOH6525
HOH6526
HOH6527
HOH6528
HOH6529
HOH6530
HOH6531
HOH6532
HOH6533
HOH6534
HOH6535
HOH6536
HOH6537
HOH6538
HOH6539
HOH6540
HOH6541
HOH6542
HOH6543
HOH6544
HOH6545
HOH6547
HOH6548
HOH6549
HOH6550
HOH6551
HOH6552
HOH6553
HOH6554
HOH6555
HOH6556
HOH6557
HOH6558
HOH6559
HOH6560
HOH6562
HOH6563
HOH6564
HOH6565
HOH6566
HOH6567
HOH6568


HOH8460
HOH8461
HOH8462
HOH8463
HOH8464
HOH8465
HOH8466
HOH8467
HOH8468
HOH8469
HOH8470
HOH8471
HOH8472
HOH8473
HOH8474
HOH8475
HOH8476
HOH8477
HOH8478
HOH8479
HOH8480
HOH8481
HOH8482
HOH8483
HOH8484
HOH8485
HOH8486
HOH8487
HOH8488
HOH8489
HOH8490
HOH8491
HOH8492
HOH8493
HOH8494
HOH8495
HOH8496
HOH8497
HOH8498
HOH8499
HOH8500
HOH8501
HOH8502
HOH8503
HOH8504
HOH8505
HOH8506
HOH8507
HOH8508
HOH8509
HOH8510
HOH8511
HOH8512
HOH8513
HOH8514
HOH8515
HOH8516
HOH8517
HOH8518
HOH8519
HOH8520
HOH8521
HOH8522
HOH8523
HOH8524
HOH8525
HOH8526
HOH8527
HOH8528
HOH8529
HOH8530
HOH8531
HOH8532
HOH8533
HOH8534
HOH8535
HOH8536
HOH8537
HOH8538
HOH8539
HOH8540
HOH8541
HOH8542
HOH8543
HOH8544
HOH8545
HOH8546
HOH8547
HOH8548
HOH8549
HOH8550
HOH8551
HOH8552
HOH8553
HOH8554
HOH8555
HOH8556
HOH8557
HOH8558
HOH8559
HOH8560
HOH8561
HOH8562
HOH8563
HOH8564
HOH8565
HOH8566
HOH8567
HOH8568
HOH8569
HOH8570
HOH8571
HOH8572
HOH8573
HOH8574
HOH8575
HOH8576
HOH8577
HOH8578
HOH8579
HOH8580
HOH8581
HOH8582
HOH8583
HOH8584


...

HOH45671
HOH45672
HOH45673
HOH45674
HOH45676
HOH45677
HOH45678
HOH45679
HOH45680
HOH45681
HOH45682
HOH45683
HOH45684
HOH45685
HOH45686
HOH45687
HOH45688
HOH45689
HOH45690
HOH45691
HOH45692
HOH45693
HOH45694
HOH45695
HOH45696
HOH45697
HOH45698
HOH45699
HOH45700
HOH45701
HOH45702
HOH45703
HOH45704
HOH45705
HOH45706
HOH45707
HOH45708
HOH45709
HOH45710
HOH45711
HOH45712
HOH45713
HOH45714
HOH45715
HOH45716
HOH45717
HOH45718
HOH45719
HOH45720
HOH45721
HOH45722
HOH45723
HOH45724
HOH45725
HOH45726
HOH45727
HOH45728
HOH45729
HOH45730
HOH45731
HOH45732
HOH45733
HOH45734
HOH45735
HOH45736
HOH45737
HOH45738
HOH45739
HOH45740
HOH45741
HOH45742
HOH45743
HOH45744
HOH45745
HOH45746
HOH45747
HOH45748
HOH45749
HOH45750
HOH45751
HOH45752
HOH45753
HOH45754
HOH45755
HOH45756
HOH45757
HOH45758
HOH45759
HOH45760
HOH45761
HOH45762
HOH45763
HOH45764
HOH45765
HOH45766
HOH45767
HOH45768
HOH45769
HOH45770
HOH45771
HOH45772
HOH45773
HOH45774
HOH45775
HOH45776
HOH45777
HOH45778
HOH45779
HOH45780
HOH45781
HOH45782
H

HOH48184
HOH48185
HOH48186
HOH48187
HOH48188
HOH48189
HOH48190
HOH48191
HOH48192
HOH48193
HOH48194
HOH48195
HOH48196
HOH48197
HOH48198
HOH48199
HOH48200
HOH48201
HOH48202
HOH48203
HOH48204
HOH48205
HOH48206
HOH48207
HOH48208
HOH48209
HOH48210
HOH48211
HOH48212
HOH48213
HOH48214
HOH48215
HOH48216
HOH48217
HOH48218
HOH48219
HOH48220
HOH48221
HOH48222
HOH48223
HOH48224
HOH48225
HOH48226
HOH48227
HOH48228
HOH48229
HOH48230
HOH48231
HOH48232
HOH48233
HOH48234
HOH48235
HOH48236
HOH48237
HOH48238
HOH48239
HOH48240
HOH48241
HOH48242
HOH48243
HOH48244
HOH48245
HOH48246
HOH48247
HOH48248
HOH48249
HOH48250
HOH48251
HOH48252
HOH48253
HOH48254
HOH48255
HOH48256
HOH48258
HOH48259
HOH48260
HOH48261
HOH48262
HOH48263
HOH48264
HOH48265
HOH48266
HOH48267
HOH48268
HOH48269
HOH48270
HOH48271
HOH48272
HOH48273
HOH48274
HOH48275
HOH48276
HOH48277
HOH48278
HOH48280
HOH48281
HOH48282
HOH48283
HOH48284
HOH48285
HOH48286
HOH48287
HOH48288
HOH48289
HOH48290
HOH48291
HOH48292
HOH48293
HOH48294
HOH48295
HOH48296
H

HOH50698
HOH50699
HOH50700
HOH50701
HOH50702
HOH50703
HOH50704
HOH50705
HOH50706
HOH50707
HOH50708
HOH50709
HOH50710
HOH50711
HOH50712
HOH50713
HOH50714
HOH50715
HOH50716
HOH50717
HOH50718
HOH50719
HOH50720
HOH50721
HOH50722
HOH50723
HOH50724
HOH50725
HOH50726
HOH50727
HOH50728
HOH50729
HOH50730
HOH50731
HOH50732
HOH50733
HOH50734
HOH50735
HOH50736
HOH50737
HOH50738
HOH50739
HOH50740
HOH50741
HOH50742
HOH50743
HOH50744
HOH50745
HOH50746
HOH50747
HOH50748
HOH50749
HOH50750
HOH50751
HOH50752
HOH50753
HOH50754
HOH50755
HOH50756
HOH50757
HOH50758
HOH50759
HOH50760
HOH50761
HOH50762
HOH50763
HOH50764
HOH50765
HOH50766
HOH50767
HOH50768
HOH50769
HOH50770
HOH50771
HOH50772
HOH50773
HOH50774
HOH50775
HOH50776
HOH50777
HOH50778
HOH50779
HOH50780
HOH50781
HOH50782
HOH50783
HOH50784
HOH50785
HOH50786
HOH50787
HOH50788
HOH50789
HOH50790
HOH50791
HOH50792
HOH50793
HOH50794
HOH50795
HOH50796
HOH50797
HOH50798
HOH50799
HOH50800
HOH50801
HOH50802
HOH50803
HOH50804
HOH50805
HOH50806
HOH50807
HOH50808
H

HOH53209
HOH53210
HOH53211
HOH53212
HOH53213
HOH53214
HOH53215
HOH53216
HOH53217
HOH53218
HOH53219
HOH53220
HOH53221
HOH53222
HOH53223
HOH53224
HOH53225
HOH53226
HOH53227
HOH53228
HOH53229
HOH53230
HOH53231
HOH53232
HOH53233
HOH53234
HOH53235
HOH53236
HOH53237
HOH53238
HOH53239
HOH53240
HOH53241
HOH53242
HOH53243
HOH53244
HOH53245
HOH53246
HOH53247
HOH53248
HOH53249
HOH53250
HOH53251
HOH53252
HOH53253
HOH53254
HOH53255
HOH53256
HOH53257
HOH53258
HOH53259
HOH53260
HOH53261
HOH53262
HOH53263
HOH53264
HOH53265
HOH53266
HOH53267
HOH53268
HOH53269
HOH53270
HOH53271
HOH53272
HOH53273
HOH53274
HOH53275
HOH53276
HOH53277
HOH53278
HOH53279
HOH53280
HOH53281
HOH53282
HOH53283
HOH53284
HOH53285
HOH53286
HOH53287
HOH53288
HOH53289
HOH53290
HOH53291
HOH53292
HOH53293
HOH53294
HOH53295
HOH53296
HOH53297
HOH53298
HOH53299
HOH53300
HOH53301
HOH53302
HOH53303
HOH53304
HOH53305
HOH53306
HOH53307
HOH53308
HOH53309
HOH53310
HOH53311
HOH53312
HOH53313
HOH53314
HOH53315
HOH53316
HOH53317
HOH53318
HOH53319
H

HOH55723
HOH55724
HOH55725
HOH55726
HOH55727
HOH55728
HOH55729
HOH55730
HOH55731
HOH55732
HOH55733
HOH55734
HOH55735
HOH55736
HOH55737
HOH55738
HOH55739
HOH55740
HOH55741
HOH55742
HOH55743
HOH55744
HOH55745
HOH55746
HOH55747
HOH55748
HOH55749
HOH55750
HOH55751
HOH55752
HOH55753
HOH55754
HOH55755
HOH55756
HOH55757
HOH55759
HOH55760
HOH55761
HOH55762
HOH55763
HOH55764
HOH55765
HOH55766
HOH55767
HOH55768
HOH55769
HOH55770
HOH55771
HOH55772
HOH55773
HOH55774
HOH55775
HOH55776
HOH55777
HOH55778
HOH55779
HOH55780
HOH55781
HOH55782
HOH55783
HOH55784
HOH55785
HOH55786
HOH55787
HOH55788
HOH55789
HOH55790
HOH55791
HOH55792
HOH55793
HOH55794
HOH55795
HOH55796
HOH55797
HOH55798
HOH55799
HOH55800
HOH55801
HOH55802
HOH55803
HOH55804
HOH55805
HOH55806
HOH55807
HOH55808
HOH55809
HOH55810
HOH55811
HOH55812
HOH55813
HOH55814
HOH55815
HOH55816
HOH55817
HOH55818
HOH55819
HOH55820
HOH55821
HOH55822
HOH55823
HOH55824
HOH55825
HOH55826
HOH55827
HOH55828
HOH55829
HOH55830
HOH55831
HOH55832
HOH55833
HOH55834
H

In [25]:
interface_pairs = []
for i, pair in enumerate(residue_pairs):
    residue_A = d[pair[0]]
    residue_B = d[pair[1]]
    print(residue_A.chain.index, residue_B.chain.index)
    if (residue_A.chain.index == 0 and residue_B.chain.index == 2) or (residue_A.chain.index == 2 and residue_B.chain.index == 0):
        print(pair)
        if distances[0][i] < 0.7:
            interface_pairs.append(pair)

0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0


0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0


0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0


0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0


0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0


...

2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2


2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2


2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2


2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2


2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2
2 2


In [23]:
distances[0][0]

0.6590759

In [59]:
# select br. complex_new and chain A within 5 of complex_new and chain C
rbd_interface_residues = ['ARG403', 'LYS417', 'VAL445', 'GLY446', 'GLY447', 'TYR449', 'TYR453', 'LEU455', 'PHE456',
                          'TYR473', 'ALA475', 'GLY476', 'SER477', 'GLU484', 'GLY485', 'PHE486', 'ASN487', 
                          'TYR489', 'PHE490', 'GLN493', 'TYR495', 'GLY496', 'PHE497', 'GLN498', 'PRO499',
                          'THR500', 'ASN501', 'GLY502', 'VAL503', 'GLY504', 'TYR505', 'GLN506'
                          ] # note had to change TYR501 to ASN501

In [60]:
len(rbd_interface_residues)

32

In [61]:
# select br. complex_new and chain C within 5 of complex_new and chain A
ace2_interface_residues = ['ILE21', 'GLN24', 'THR27', 'PHE28', 'ASP30', 'LYS31', 'PHE32', 'HIS34', 'GLU35', 'GLU37', 
                           'ASP38', 'TYR41', 'GLN42', 'LEU45', 'ASN49', 'GLN76', 'LEU79', 'ALA80', 'MET82', 'TYR83',
                            'THR324', 'GLN325', 'GLY326', 'GLU329', 'ASN330', 
                           'LEU351', 'GLY352', 'LYS353', 'GLY354', 'ASP355', 'PHE356', 'ARG357',
                          'ALA386', 'ARG393']

In [62]:
len(ace2_interface_residues)

34

In [93]:
rest_atoms = []
n_residues = 0
for entry in rbd_interface_residues + ace2_interface_residues:
    for res in htf.hybrid_topology.residues:
        if res.resSeq == int(entry[3:]) and res.name == entry[:3]:
            if entry == 'ARG357':
                if res.chain.index == 2:
                    print(res)
                    n_residues += 1
                    atoms = [atom.index for atom in res.atoms]
                    rest_atoms += atoms
            else:
                print(res)
                n_residues += 1
                atoms = [atom.index for atom in res.atoms]
                rest_atoms += atoms
                if res.resSeq == 501 and res.name == 'ASN':
                    print(len(atoms))
                

ARG403
LYS417
VAL445
GLY446
GLY447
TYR449
TYR453
LEU455
PHE456
TYR473
ALA475
GLY476
SER477
GLU484
GLY485
PHE486
ASN487
TYR489
PHE490
GLN493
TYR495
GLY496
PHE497
GLN498
PRO499
THR500
ASN501
28
GLY502
VAL503
GLY504
TYR505
GLN506
ILE21
GLN24
THR27
PHE28
ASP30
LYS31
PHE32
HIS34
GLU35
GLU37
ASP38
TYR41
GLN42
LEU45
ASN49
GLN76
LEU79
ALA80
MET82
TYR83
THR324
GLN325
GLY326
GLU329
ASN330
LEU351
GLY352
LYS353
GLY354
ASP355
PHE356
ARG357
ALA386
ARG393


In [88]:
n_residues

66

In [94]:
len(rest_atoms)

1059

In [84]:
for atom in rest_atoms:
    print(atom)

1087
1088
1089
1090
1091
1092
1093
1094
1095
1096
1097
1098
1099
1100
1101
1102
1103
1104
1105
1106
1107
1108
1109
1110
1290
1291
1292
1293
1294
1295
1296
1297
1298
1299
1300
1301
1302
1303
1304
1305
1306
1307
1308
1309
1310
1311
1725
1726
1727
1728
1729
1730
1731
1732
1733
1734
1735
1736
1737
1738
1739
1740
1741
1742
1743
1744
1745
1746
1747
1748
1749
1750
1751
1752
1753
1754
1769
1770
1771
1772
1773
1774
1775
1776
1777
1778
1779
1780
1781
1782
1783
1784
1785
1786
1787
1788
1789
1844
1845
1846
1847
1848
1849
1850
1851
1852
1853
1854
1855
1856
1857
1858
1859
1860
1861
1862
1863
1864
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
2203
2204
2205
2206
2207
2208
2209
2210
2211
2212
2213
2214
2215
2216
2217
2218
2219
2220
2221
2222
2223
2241
2242
2243
2244
2245
2246
2247
2248
2249
2250
2251
2252
2253
2254
2255
2256
2257
2258
2259
2260
2261
2262


In [65]:
# Get REST region
for res in htf.hybrid_topology.residues:
    if res.resSeq == 501 and res.chain.index == 0:
        mutated_res = res


In [66]:
query_indices = [atom.index for atom in mutated_res.atoms]
traj = md.Trajectory(np.array(positions), htf.hybrid_topology)
solute_atoms = list(traj.topology.select("is_protein"))
rest_atoms = list(md.compute_neighbors(traj, 0.3, query_indices, haystack_indices=solute_atoms)[0])

In [74]:
query_indices

[2605,
 2606,
 2607,
 2608,
 2609,
 2610,
 2611,
 2612,
 2613,
 2614,
 2615,
 2616,
 2617,
 2618,
 185377,
 185378,
 185379,
 185380,
 185381,
 185382,
 185383,
 185384,
 185385,
 185386,
 185387,
 185388,
 185389,
 185390]

In [67]:
len(rest_atoms)

75

In [80]:
for atom in rest_atoms:
    print(atom)

1087
1088
1089
1090
1091
1092
1093
1094
1095
1096
1097
1098
1099
1100
1101
1102
1103
1104
1105
1106
1107
1108
1109
1110
1290
1291
1292
1293
1294
1295
1296
1297
1298
1299
1300
1301
1302
1303
1304
1305
1306
1307
1308
1309
1310
1311
1725
1726
1727
1728
1729
1730
1731
1732
1733
1734
1735
1736
1737
1738
1739
1740
1741
1742
1743
1744
1745
1746
1747
1748
1749
1750
1751
1752
1753
1754
1769
1770
1771
1772
1773
1774
1775
1776
1777
1778
1779
1780
1781
1782
1783
1784
1785
1786
1787
1788
1789
1844
1845
1846
1847
1848
1849
1850
1851
1852
1853
1854
1855
1856
1857
1858
1859
1860
1861
1862
1863
1864
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
2203
2204
2205
2206
2207
2208
2209
2210
2211
2212
2213
2214
2215
2216
2217
2218
2219
2220
2221
2222
2223
2241
2242
2243
2244
2245
2246
2247
2248
2249
2250
2251
2252
2253
2254
2255
2256
2257
2258
2259
2260
2261
2262


In [68]:
query_indices = [atom.index for index in residues_indexes for atom in .atoms]


In [69]:
len(traj.topology.select(selection))

1059

In [72]:
for atom in htf.hybrid_topology.atoms:
    if atom.residue.resSeq == 501 and atom.residue.name == 'ASN':
        print(atom.index, atom)

2605 ASN501-N
2606 ASN501-H
2607 ASN501-CA
2608 ASN501-HA
2609 ASN501-C
2610 ASN501-O
2611 ASN501-CB
2612 ASN501-HB2
2613 ASN501-HB3
2614 ASN501-CG
2615 ASN501-ND2
2616 ASN501-HD21
2617 ASN501-HD22
2618 ASN501-OD1
185377 ASN501-CD2
185378 ASN501-HD2
185379 ASN501-HB2
185380 ASN501-HB3
185381 ASN501-CG
185382 ASN501-CD1
185383 ASN501-HD1
185384 ASN501-CE1
185385 ASN501-HE1
185386 ASN501-CZ
185387 ASN501-OH
185388 ASN501-HH
185389 ASN501-CE2
185390 ASN501-HE2


In [78]:
for residue in htf.hybrid_topology.residues:
    if residue.resSeq == 501 and residue.name == 'ASN':
        for atom in residue.atoms:
            print(atom.index, atom)

2605 ASN501-N
2606 ASN501-H
2607 ASN501-CA
2608 ASN501-HA
2609 ASN501-C
2610 ASN501-O
2611 ASN501-CB
2612 ASN501-HB2
2613 ASN501-HB3
2614 ASN501-CG
2615 ASN501-ND2
2616 ASN501-HD21
2617 ASN501-HD22
2618 ASN501-OD1
185377 ASN501-CD2
185378 ASN501-HD2
185379 ASN501-HB2
185380 ASN501-HB3
185381 ASN501-CG
185382 ASN501-CD1
185383 ASN501-HD1
185384 ASN501-CE1
185385 ASN501-HE1
185386 ASN501-CZ
185387 ASN501-OH
185388 ASN501-HH
185389 ASN501-CE2
185390 ASN501-HE2


In [73]:
for atom in traj.topology.select(selection):
    print(atom)

1087
1088
1089
1090
1091
1092
1093
1094
1095
1096
1097
1098
1099
1100
1101
1102
1103
1104
1105
1106
1107
1108
1109
1110
1290
1291
1292
1293
1294
1295
1296
1297
1298
1299
1300
1301
1302
1303
1304
1305
1306
1307
1308
1309
1310
1311
1725
1726
1727
1728
1729
1730
1731
1732
1733
1734
1735
1736
1737
1738
1739
1740
1741
1742
1743
1744
1745
1746
1747
1748
1749
1750
1751
1752
1753
1754
1769
1770
1771
1772
1773
1774
1775
1776
1777
1778
1779
1780
1781
1782
1783
1784
1785
1786
1787
1788
1789
1844
1845
1846
1847
1848
1849
1850
1851
1852
1853
1854
1855
1856
1857
1858
1859
1860
1861
1862
1863
1864
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
2203
2204
2205
2206
2207
2208
2209
2210
2211
2212
2213
2214
2215
2216
2217
2218
2219
2220
2221
2222
2223
2241
2242
2243
2244
2245
2246
2247
2248
2249
2250
2251
2252
2253
2254
2255
2256
2257
2258
2259
2260
2261
2262
